In [1]:
print("hello")

hello


In [ ]:
"""
the following endpoint should work as well https://rapidapi.com/mahmudulhasandev/api/amazon-product-advertising-api

need 2000 requests per month per gpu

48 000 requests in total so when paying the money this would be totally enough

using keepa now i guess i need to get the api key and then i am ready to go

i guess lest
"""

In [3]:
import requests
import json
import datetime

def get_full_price_history(api_key, asin, domain=1):
    """
    Retrieves complete price history for a product using Keepa API.

    Parameters:
    - api_key: Your Keepa API key.
    - asin: The Amazon ASIN for the product.
    - domain: Amazon domain ID (1=US, 2=UK, 3=DE, etc.).

    Returns:
    - Dictionary containing product info and price history, or an error message.
    """

    # Build the URL - request full history with stats, buybox, and rating info
    base_url = "https://api.keepa.com/product"
    params = {
        'key': api_key,
        'domain': domain,
        'asin': asin,
        'stats': '2011-01-01,2025-01-01', # Ensures stats cover the entire history
        'history': 1,                     # Explicitly include historical data
        'buybox': 1,                      # Include Buy Box history (+2 tokens)
        'rating': 1                       # Include Rating history (+1 token)
    }

    print(f"Requesting Keepa URL: {base_url} with params: {params}") # For debugging

    try:
        response = requests.get(base_url, params=params)
        response.raise_for_status() # Raise an exception for bad status codes (4xx or 5xx)
        data = response.json()

        if "products" in data and len(data["products"]) > 0:
            product = data["products"][0]

            # Process the price history from the 'csv' field
            if "csv" in product:
                price_history = product["csv"]
                processed_history = {}

                # Define price types we want to process
                price_types = {
                    "AMAZON": "amazon_prices",
                    "NEW": "new_prices",
                    "USED": "used_prices",
                    # Add other types like 'SALES', 'LISTPRICE' if needed
                }

                for keepa_type, output_key in price_types.items():
                    processed_history[output_key] = []
                    if keepa_type in price_history and price_history[keepa_type]:
                        # Data is [timestamp1, price1, timestamp2, price2, ...]
                        raw_list = price_history[keepa_type]
                        for i in range(0, len(raw_list), 2):
                             # Check if the next element exists before accessing
                            if i + 1 < len(raw_list):
                                # Keepa time = minutes since Jan 1, 2000
                                # Convert Keepa time to Unix timestamp (seconds since epoch)
                                keepa_minutes = raw_list[i]
                                # Keepa epoch starts on 2000-01-01 UTC
                                keepa_epoch_start = datetime.datetime(2000, 1, 1, tzinfo=datetime.timezone.utc)
                                # Add the minutes to get the actual timestamp
                                timestamp = keepa_epoch_start + datetime.timedelta(minutes=keepa_minutes)

                                # Price is in cents/smallest unit, divide by 100 for dollars/euros etc.
                                price_cents = raw_list[i+1]
                                price = price_cents / 100.0 if price_cents > 0 else None # Handle -1 for OOS

                                processed_history[output_key].append({
                                    "date": timestamp.strftime("%Y-%m-%d %H:%M:%S"), # More precise timestamp
                                    "price": price
                                })


                return {
                    "product_title": product.get("title", "N/A"),
                    "asin": product.get("asin", "N/A"),
                    **processed_history, # Merge processed price histories
                    "raw_keepa_product_data": product # Include raw data for reference
                }
            else:
                 return {"error": "No price history data ('csv' field) found in the response."}
        elif "error" in data:
             # Handle specific Keepa API errors
             return {"error": f"Keepa API Error: {data['error']['message']}"}
        else:
            # Handle cases where the product might not be found or other issues
            return {"error": f"Product ASIN {asin} not found or invalid response."}

    except requests.exceptions.RequestException as e:
        return {"error": f"API request failed: {str(e)}"}
    except json.JSONDecodeError:
        return {"error": "Failed to decode JSON response from Keepa."}
    except Exception as e:
         # Catch any other unexpected errors
        return {"error": f"An unexpected error occurred: {str(e)}"}


# --- Usage ---
# IMPORTANT: Replace with your REAL Keepa API key
api_key = "bdmmpr7jl1pq9iopubktrp53a9r31m4otho1btpd5fv10n30lf8hje1c3ah3vdng"
gpu_asin = "B08HR6ZBYJ" # RTX 3090 FE

# Get the price history
price_data = get_full_price_history(api_key, gpu_asin)

# Print the result (pretty-printed JSON)
print(json.dumps(price_data, indent=2, default=str)) # Use default=str for datetime objects

Requesting Keepa URL: https://api.keepa.com/product with params: {'key': 'bdmmpr7jl1pq9iopubktrp53a9r31m4otho1btpd5fv10n30lf8hje1c3ah3vdng', 'domain': 1, 'asin': 'B08HR6ZBYJ', 'stats': '2011-01-01,2025-01-01', 'history': 1, 'buybox': 1, 'rating': 1}
{
  "product_title": "Nvidia GeForce RTX 3090 Founders Edition Graphics Card",
  "asin": "B08HR6ZBYJ",
  "amazon_prices": [],
  "new_prices": [],
  "used_prices": [],
  "raw_keepa_product_data": {
    "csv": [
      [
        5108588,
        -1
      ],
      [
        5108588,
        -1,
        5112412,
        199999,
        5113488,
        -1,
        5122116,
        399900,
        5125086,
        349900,
        5134740,
        299999,
        5135312,
        339999,
        5136090,
        319999,
        5137912,
        318800,
        5140004,
        300000,
        5143066,
        318800,
        5143440,
        309900,
        5144724,
        318800,
        5146272,
        290000,
        5146998,
        309900,


In [2]:
import requests
import json

# --- Configuration ---
# IMPORTANT: Replace with your REAL Keepa API key
api_key = "bdmmpr7jl1pq9iopubktrp53a9r31m4otho1btpd5fv10n30lf8hje1c3ah3vdng"
gpu_asin = "B08HR6ZBYJ" # RTX 3090 FE
domain_id = 1          # 1 = amazon.com

# --- Build the API Request URL ---
# Basic request - just gets product data, minimal token cost (1 token)
base_url = "https://api.keepa.com/product"
params = {
    'key': api_key,
    'domain': domain_id,
    'asin': gpu_asin
    # Add other parameters here later if needed, e.g.:
    # 'history': 1,
    # 'stats': '2011-01-01,2025-01-01',
}

print(f"--- Requesting Keepa API ---")
print(f"URL: {base_url}")
print(f"Parameters: {params}")
print("-" * 30)

# --- Make the API Request and Print Raw Response ---
try:
    response = requests.get(base_url, params=params)
    response.raise_for_status() # Check for HTTP errors (like 401 Unauthorized, 404 Not Found, etc.)

    # Get the JSON data from the response
    raw_data = response.json()

    print("--- Full Raw JSON Response from Keepa ---")
    # Use json.dumps for pretty printing
    print(json.dumps(raw_data, indent=2))
    print("-" * 30)

except requests.exceptions.HTTPError as http_err:
    print(f"HTTP error occurred: {http_err}")
    print(f"Response status code: {response.status_code}")
    try:
        # Try to print the error response body if available
        error_details = response.json()
        print("Error details from Keepa:")
        print(json.dumps(error_details, indent=2))
    except json.JSONDecodeError:
        print("Could not decode error response as JSON.")
        print(f"Raw error response text: {response.text}")
except requests.exceptions.RequestException as req_err:
    print(f"Request error occurred: {req_err}")
except json.JSONDecodeError:
    print("Error: Failed to decode the response from Keepa as JSON.")
    print(f"Raw response text: {response.text}")
except Exception as e:
    print(f"An unexpected error occurred: {e}")

--- Requesting Keepa API ---
URL: https://api.keepa.com/product
Parameters: {'key': 'bdmmpr7jl1pq9iopubktrp53a9r31m4otho1btpd5fv10n30lf8hje1c3ah3vdng', 'domain': 1, 'asin': 'B08HR6ZBYJ'}
------------------------------
--- Full Raw JSON Response from Keepa ---
{
  "timestamp": 1745501467920,
  "tokensLeft": 799,
  "refillIn": 43400,
  "refillRate": 20,
  "tokenFlowReduction": 0.0,
  "tokensConsumed": 1,
  "processingTimeInMs": 12,
  "products": [
    {
      "csv": [
        [
          5108588,
          -1
        ],
        [
          5108588,
          -1,
          5112412,
          199999,
          5113488,
          -1,
          5122116,
          399900,
          5125086,
          349900,
          5134740,
          299999,
          5135312,
          339999,
          5136090,
          319999,
          5137912,
          318800,
          5140004,
          300000,
          5143066,
          318800,
          5143440,
          309900,
          5144724,
          3

In [4]:
import requests
import json
import csv
import datetime

# --- Configuration ---
# IMPORTANT: Replace with your REAL Keepa API key
api_key = "bdmmpr7jl1pq9iopubktrp53a9r31m4otho1btpd5fv10n30lf8hje1c3ah3vdng"
gpu_asin = "B08HR6ZBYJ" # RTX 3090 FE
domain_id = 1          # 1 = amazon.com
output_csv_file = f"{gpu_asin}_price_history.csv"
# Choose the price type you want to export:
# Common options: 'NEW', 'AMAZON', 'USED'
price_type_to_export = 'NEW'

# Keepa epoch starts on 2000-01-01 00:00:00 UTC
keepa_epoch_start = datetime.datetime(2000, 1, 1, tzinfo=datetime.timezone.utc)

def get_keepa_product_data(api_key, asin, domain):
    """Fetches product data from Keepa API."""
    base_url = "https://api.keepa.com/product"
    params = {
        'key': api_key,
        'domain': domain,
        'asin': asin,
        'history': 1 # Ensure historical data is included
    }
    print(f"Requesting data for ASIN {asin} from Keepa...")
    try:
        response = requests.get(base_url, params=params)
        response.raise_for_status() # Check for HTTP errors
        print("Data received successfully.")
        return response.json()
    except requests.exceptions.HTTPError as http_err:
        print(f"HTTP error occurred: {http_err}")
        try:
            error_details = response.json()
            print(f"Keepa Error: {error_details.get('error', {}).get('message', 'Unknown error')}")
        except json.JSONDecodeError:
            print(f"Raw error response: {response.text}")
        return None
    except requests.exceptions.RequestException as req_err:
        print(f"Request error occurred: {req_err}")
        return None
    except json.JSONDecodeError:
        print("Error: Failed to decode the response from Keepa as JSON.")
        print(f"Raw response text: {response.text}")
        return None
    except Exception as e:
        print(f"An unexpected error occurred during API request: {e}")
        return None

def process_price_history(product_data, price_type):
    """Extracts and formats price history from Keepa data."""
    processed_data = []
    if not product_data or "products" not in product_data or not product_data["products"]:
        print("Error: Invalid or empty product data received.")
        return processed_data

    product = product_data["products"][0]

    if "csv" not in product or price_type not in product["csv"]:
        print(f"Error: Price type '{price_type}' not found in the 'csv' data for ASIN {product.get('asin', 'N/A')}.")
        return processed_data

    # Raw history is [timestamp1, price1, timestamp2, price2, ...]
    raw_history = product["csv"][price_type]

    if not raw_history:
        print(f"No historical data found for price type '{price_type}'.")
        return processed_data

    print(f"Processing '{price_type}' price history...")
    for i in range(0, len(raw_history), 2):
         # Check if the next element exists before accessing
        if i + 1 < len(raw_history):
            keepa_minutes = raw_history[i]
            price_cents = raw_history[i+1]

            # Skip entries where the product was Out Of Stock (-1)
            if price_cents == -1:
                continue

            # Convert Keepa time (minutes since 2000-01-01) to datetime
            timestamp = keepa_epoch_start + datetime.timedelta(minutes=keepa_minutes)
            # Format date as YYYY-MM-DD
            formatted_date = timestamp.strftime('%Y-%m-%d')

            # Convert price (cents/smallest unit) to dollars/euros etc.
            price = price_cents / 100.0

            processed_data.append([formatted_date, price])

    print(f"Processed {len(processed_data)} valid price points.")
    return processed_data

def save_to_csv(data, filename):
    """Saves the processed data to a CSV file."""
    if not data:
        print("No data to save.")
        return

    print(f"Saving data to {filename}...")
    try:
        with open(filename, 'w', newline='', encoding='utf-8') as csvfile:
            writer = csv.writer(csvfile)
            # Write header
            writer.writerow(['Date', 'Price'])
            # Write data rows
            writer.writerows(data)
        print("CSV file saved successfully.")
    except IOError as e:
        print(f"Error writing to CSV file {filename}: {e}")
    except Exception as e:
        print(f"An unexpected error occurred during CSV writing: {e}")


# --- Main Execution ---
if __name__ == "__main__":
    keepa_data = get_keepa_product_data(api_key, gpu_asin, domain_id)

    if keepa_data:
        price_list = process_price_history(keepa_data, price_type_to_export)
        save_to_csv(price_list, output_csv_file)
    else:
        print("Failed to retrieve data from Keepa. CSV file not created.")

Requesting data for ASIN B08HR6ZBYJ from Keepa...
Data received successfully.
Error: Price type 'NEW' not found in the 'csv' data for ASIN B08HR6ZBYJ.
No data to save.


In [5]:
import json
import csv
import datetime
import os
import pprint

# Path to your JSON data file
json_file_path = 'test.json'
output_directory = 'price_history'

# Create output directory if it doesn't exist
if not os.path.exists(output_directory):
    os.makedirs(output_directory, exist_ok=True)

# Keepa epoch starts on 2000-01-01 00:00:00 UTC
keepa_epoch_start = datetime.datetime(2000, 1, 1, tzinfo=datetime.timezone.utc)

def convert_keepa_time(keepa_minutes):
    """Convert Keepa time (minutes since 2000-01-01) to a datetime object"""
    return keepa_epoch_start + datetime.timedelta(minutes=keepa_minutes)

def convert_keepa_price(price_cents):
    """Convert Keepa price (cents/smallest unit) to dollars/euros"""
    if price_cents == -1:  # Out of stock
        return None
    return price_cents / 100.0

def process_price_history(raw_data, asin):
    """Process the price history data from the raw JSON"""
    if not raw_data or "products" not in raw_data or not raw_data["products"]:
        print("Error: No product data found in the JSON")
        return {}
    
    product = raw_data["products"][0]
    
    if "csv" not in product:
        print("Error: No price history data found in the product")
        return {}
    
    # Access the csv data
    csv_data = product["csv"]
    
    # Debug: Print the structure of csv_data
    print("CSV data structure:")
    data_type = type(csv_data)
    print(f"Type: {data_type}")
    
    if isinstance(csv_data, list):
        print(f"List length: {len(csv_data)}")
        if len(csv_data) > 0:
            print(f"First element type: {type(csv_data[0])}")
            if isinstance(csv_data[0], list):
                print(f"First element length: {len(csv_data[0])}")
    
    # If csv is a list, extract the price history from the nested lists
    # based on the structure revealed in test.json
    if isinstance(csv_data, list):
        print("Processing list-formatted CSV data")
        
        # The data appears to be in the first element
        if len(csv_data) > 0 and isinstance(csv_data[0], list):
            return process_list_price_data(csv_data)
        
    elif isinstance(csv_data, dict):
        return process_dict_price_data(csv_data)
    else:
        print(f"Error: Unexpected csv data format: {type(csv_data)}")
        return {}

def process_list_price_data(csv_data):
    """Process price history from list-formatted CSV data"""
    result = {}
    
    # Process each element in the csv_data list
    for idx, price_data in enumerate(csv_data):
        if not isinstance(price_data, list):
            continue
            
        # Skip empty lists
        if not price_data:
            continue
            
        price_type = f"DATA_{idx}"
        print(f"Processing {price_type} with {len(price_data)} data points")
        
        processed_data = []
        # Look for alternating timestamp/price pairs
        timestamps_and_prices = []
        
        # Check if data is already paired or needs pairing
        if len(price_data) >= 2 and all(isinstance(x, (int, float)) for x in price_data[:10]):
            # Data needs pairing (format: [ts1, price1, ts2, price2, ...])
            for i in range(0, len(price_data), 2):
                if i + 1 < len(price_data):
                    timestamps_and_prices.append((price_data[i], price_data[i+1]))
        elif len(price_data) > 0 and isinstance(price_data[0], list) and len(price_data[0]) == 2:
            # Data is already paired (format: [[ts1, price1], [ts2, price2], ...])
            timestamps_and_prices = price_data
            
        # Process the timestamp/price pairs
        for timestamp, price in timestamps_and_prices:
            # Skip entries without valid data
            if timestamp is None or price is None:
                continue
                
            # Convert timestamp to datetime
            date = convert_keepa_time(timestamp)
            
            # Skip out of stock entries (typical value is -1)
            if price == -1:
                continue
                
            # Convert price from cents to dollars/euros
            value = convert_keepa_price(price)
            
            processed_data.append({
                'date': date.strftime('%Y-%m-%d'),
                'value': value
            })
        
        if processed_data:
            result[price_type] = processed_data
            print(f"  Processed {len(processed_data)} valid price points")
    
    return result

def process_dict_price_data(csv_data):
    """Process price history from dictionary-formatted CSV data"""
    print("Processing dictionary-formatted CSV data")
    available_price_types = list(csv_data.keys())
    print(f"Available price types: {available_price_types}")
    
    # Process each available price type
    result = {}
    for price_type in available_price_types:
        print(f"Processing {price_type} price history...")
        
        # Get the raw history data (alternating timestamp and price)
        history_data = csv_data[price_type]
        
        # Skip empty data
        if not history_data:
            print(f"No data available for {price_type}")
            continue
        
        # Process the data into pairs
        processed_data = []
        for i in range(0, len(history_data), 2):
            if i + 1 < len(history_data):
                timestamp = history_data[i]
                price = history_data[i+1]
                
                # Convert timestamp to datetime
                date = convert_keepa_time(timestamp)
                
                # Convert price (skip out of stock if needed)
                if price_type != 'SALES' and price == -1:
                    # Skip out of stock entries for regular price types
                    continue
                
                # For sales rank, just use the raw value
                # For prices, convert from cents to dollars/euros
                if price_type == 'SALES':
                    value = price  # Sales rank is the integer value itself
                else:
                    value = convert_keepa_price(price)
                    
                processed_data.append({
                    'date': date.strftime('%Y-%m-%d'),
                    'value': value
                })
        
        result[price_type] = processed_data
        print(f"  Processed {len(processed_data)} data points")
    
    return result

def save_to_csv(data, asin):
    """Save processed data to CSV files"""
    if not data:
        print("No data to save")
        return
        
    for price_type, history in data.items():
        if not history:
            continue
            
        filename = f"{output_directory}/{asin}_{price_type}_history.csv"
        
        print(f"Saving {price_type} history to {filename}...")
        with open(filename, 'w', newline='', encoding='utf-8') as csvfile:
            fieldnames = ['date', 'value']
            writer = csv.DictWriter(csvfile, fieldnames=fieldnames)
            
            writer.writeheader()
            for entry in history:
                writer.writerow(entry)
        
        print(f"  Saved {len(history)} rows")

def main():
    print("Loading JSON data...")
    with open(json_file_path, 'r', encoding='utf-8') as f:
        data = json.load(f)
    
    # Get the ASIN from the data
    if "products" in data and len(data["products"]) > 0:
        asin = data["products"][0].get("asin", "UNKNOWN")
    else:
        asin = "UNKNOWN"
    
    print(f"Processing data for ASIN: {asin}")
    
    # Process the price history
    price_history = process_price_history(data, asin)
    
    # Save to CSV files
    save_to_csv(price_history, asin)
    
    print("Processing complete!")

if __name__ == "__main__":
    main()

Loading JSON data...
Processing data for ASIN: B08HR6ZBYJ
CSV data structure:
Type: <class 'list'>
List length: 34
First element type: <class 'list'>
First element length: 2
Processing list-formatted CSV data
Processing DATA_0 with 2 data points
Processing DATA_1 with 5158 data points
  Processed 2536 valid price points
Processing DATA_2 with 2030 data points
  Processed 949 valid price points
Processing DATA_3 with 2 data points
Processing DATA_4 with 798 data points
  Processed 287 valid price points
Processing DATA_11 with 8714 data points
  Processed 4318 valid price points
Processing DATA_12 with 2434 data points
  Processed 1149 valid price points
Saving DATA_1 history to price_history/B08HR6ZBYJ_DATA_1_history.csv...
  Saved 2536 rows
Saving DATA_2 history to price_history/B08HR6ZBYJ_DATA_2_history.csv...
  Saved 949 rows
Saving DATA_4 history to price_history/B08HR6ZBYJ_DATA_4_history.csv...
  Saved 287 rows
Saving DATA_11 history to price_history/B08HR6ZBYJ_DATA_11_history.csv

In [ ]:
"""
in the next step i need to take the data and then i need to somehow prepare it so that i can put it on the website later

for now all the data i need is the pricing data of the product
"""